In [ ]:
# %%capture
# # Skip restarting message in Colab
# import sys; modules = list(sys.modules.keys())
# for x in modules: sys.modules.pop(x) if "PIL" in x or "google" in x else None

# !pip install unsloth vllm
# !pip install --upgrade pillow
# # If you are running this notebook on local, you need to install `diffusers` too
# # !pip install diffusers
# # Temporarily install a specific TRL nightly version
# !pip install git+https://github.com/huggingface/trl.git@e95f9fb74a3c3647b86f251b7e230ec51c64b72b

In [ ]:
# %pip uninstall unsloth unsloth_zoo -y
# %pip install --upgrade --no-cache-dir "unsloth[colab-new] @ git+https://github.com/unslothai/unsloth.git"
# %pip install --upgrade --no-cache-dir "git+https://github.com/unslothai/unsloth-zoo.git"


In [ ]:
# %pip install git+https://github.com/huggingface/trl.git@e95f9fb74a3c3647b86f251b7e230ec51c64b72b

In [ ]:
from unsloth import FastLanguageModel
# PatchFastRL("GRPO", FastLanguageModel)

In [ ]:
from unsloth import is_bfloat16_supported
import torch
from peft import PeftModel
max_seq_length = 2500 # Can increase for longer reasoning traces
lora_rank = 32 # Larger rank = smarter, but slower


#unsloth/Qwen2.5-3B-unsloth-bnb-4bit
#"unsloth/DeepSeek-R1-Distill-Qwen-7B-unsloth-bnb-4bit",
model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = "unsloth/Qwen2.5-3B-Instruct-bnb-4bit",
    # model_name = "./outputs/checkpoint-100",
    max_seq_length = max_seq_length,
    load_in_4bit = True, # False for LoRA 16bit
    fast_inference = True, # Enable vLLM fast inference
    max_lora_rank = lora_rank,
    gpu_memory_utilization = 0.6, # Reduce if out of memory
)

# 如果已有训练好的LoRA适配器

model = FastLanguageModel.get_peft_model(
    model,
    r = lora_rank, # Choose any number > 0 ! Suggested 8, 16, 32, 64, 128
    target_modules = [
        "q_proj", "k_proj", "v_proj", "o_proj",
        "gate_proj", "up_proj", "down_proj",
    ], # Remove QKVO if out of memory
    lora_alpha = lora_rank,
    use_gradient_checkpointing = "unsloth", # Enable long context finetuning
    random_state = 3407,
   
)

active_adapter = model.active_adapter
model.load_adapter('qwen_3_25', active_adapter, is_trainable=True)


In [ ]:
import re
from datasets import load_dataset, Dataset
import multiprocessing



#3.将思考过程转化为可执行的Python代码,print(答案)（<code>标签内）  \n<code>\n...\n</code>

def check_answer_tags(text):
    return '<answer>' in text and '</answer>' in text
def check_code_tags(text):
    return '<code>' in text and '</code>' in text

def extract_xml_answer(text: str) -> str:
    if check_answer_tags(text):
        answer = text.split("<answer>")[-1]
        answer = answer.split("</answer>")[0]
        return answer.strip()
    else:
        return ''
def extract_xml_code(text: str) -> str:
    if check_code_tags(text):
        answer = text.split("<code>")[-1]
        answer = answer.split("</code>")[0]
        return answer.strip()
    else:
        return ''

def extract_hash_answer(text: str) -> str | None:
    if "####" not in text:
        return None
    return text.split("####")[1].strip()

# uncomment middle messages for 1-shot prompting

#可选 'digit', 'one_d_array', 'two_d_array'。

def parse_number_simple(s):
    s_clean = s.replace(',', '')
    try:
        return float(s_clean) if '.' in s_clean else int(s_clean)
    except ValueError:
        raise ValueError(f"Could not convert '{s}' to number")

# 示例
# print(parse_number_simple("123,45"))   # 12345（即使逗号位置不规范）
# print(parse_number_simple("12.34"))    # 12.34
# parse_number_simple("12a,34")       # 抛出 ValueError

def get_gsm8k_questions(split = "train") -> Dataset:
    data = load_dataset('openai/gsm8k', 'main')[split] # type: ignore
    data = data.select(range(500, len(data)))
    data = data.map(lambda x: { # type: ignore
        'prompt': [
            {'role': 'system', 'content': SYSTEM_PROMPT},
            {'role': 'user', 'content': x['question']}
        ],
        'answer': parse_number_simple(extract_hash_answer(x['answer'])),
        'answer_type':'digit'
    }) # type: ignore
    return data # type: ignore



# def compare_arrays(arr1, arr2):
#     return arr1 == arr2
# import ast

# def validate_numeric_array(s):
#     try:
#         parsed = ast.literal_eval(s)
#     except (SyntaxError, ValueError):
#         return False
    
#     # 外层必须是列表
#     if not isinstance(parsed, list):
#         return False
    
#     # 检查每个内层元素是否为列表且包含数字
#     for inner in parsed:
#         if not isinstance(inner, list):
#             return False
#         for item in inner:
#             if not isinstance(item, (int, float)):
#                 return False
    
#     return True
# Reward functions
def correctness_reward_func(prompts, completions, answer, **kwargs) -> list[float]:
    responses = [completion[0]['content'] for completion in completions]
    q = prompts[0][-1]['content']
    extracted_responses = [extract_xml_answer(r) for r in responses]
    print('-'*20, f"Question:\n{q}", f"\nAnswer:\n{answer[0]}", f"\nResponse:\n{responses[0]}", f"\nExtracted:\n{extracted_responses[0]}")
    result=[2.0 if validate_numeric_array(r) and compare_arrays(eval(r),a) else 0.0 for r, a in zip(extracted_responses, answer)]
    print(result)
    return result

# def correctness_reward_func(prompts, completions, answer, **kwargs) -> list[float]:
#     responses = [completion[0]['content'] for completion in completions]
#     q = prompts[0][-1]['content']
#     extracted_responses = [extract_xml_answer(r) for r in responses]
    
#     result = [2.0 if validate_numeric_array(r) and compare_arrays(eval(r), a) else 0.0 for r, a in zip(extracted_responses, answer)]
    
#     # 打印得分2.0的样本信息
#     for i, score in enumerate(result):
#         if score == 2.0:
#             print('-'*20)
#             print(f"Question:\n{q}")
#             print(f"Answer:\n{answer[i]}")
#             print(f"Response:\n{responses[i]}")
#             print(f"Extracted:\n{extracted_responses[i]}")
    
#     print(result)
#     return result


def int_reward_func(completions, **kwargs) -> list[float]:
    responses = [completion[0]['content'] for completion in completions]
    extracted_responses = [extract_xml_answer(r) for r in responses]
    return [0.5 if validate_numeric_array(r) else 0.0 for r in extracted_responses]





def count_xml(text) -> float:
    count = 0.0
    if text.count("<think>\n") == 1:
        count += 0.2
    if text.count("\n</think>\n") == 1:
        count += 0.2
    if text.count("\n<answer>\n") == 1:
        count += 0.2
        # count -= len(text.split("\n</answer>\n")[-1])*0.001
    if text.count("\n</answer>") == 1:
        count += 0.2
        # count -= (len(text.split("\n</answer>")[-1]) - 1)*0.001
    if text.count("\n<code>\n") == 1:
        count += 0.125
    if text.count("\n</code>") == 1:
        count += 0.125
       
    # if 'print' in extract_xml_code(text):
    #     count+=0.2
    return count

def xmlcount_reward_func(completions, **kwargs) -> list[float]:
    contents = [completion[0]["content"] for completion in completions]
    # print(contents[0])
    return [count_xml(c) for c in contents]
def is_language_consistent(text, threshold=0.1, main_lang="chinese"):
    """判断文本语言是否一致（要求主要语言字符不低于指定比例）
    
    Args:
        text: 待检测文本
        threshold: 主要语言最低要求比例，默认95%
        main_lang: 指定主要语言（可选），如'chinese'、'japanese_kana'等
        
    Returns:
        bool: 是否语言一致
    """
    # 定义各语言的Unicode范围（前闭后开区间）
    language_blocks = {
        'chinese': [
            (0x4E00, 0x9FFF+1),        # CJK Unified Ideographs
            (0x3400, 0x4DBF+1),        # CJK Extension A
            (0x20000, 0x2A6DF+1),      # CJK Extension B
            (0xF900, 0xFAFF+1),        # CJK Compatibility Ideographs
        ],
        'japanese_kana': [
            (0x3040, 0x309F+1),        # Hiragana
            (0x30A0, 0x30FF+1),        # Katakana
        ],
        'korean': [
            (0xAC00, 0xD7AF+1),        # Hangul Syllables
            (0x1100, 0x11FF+1),        # Hangul Jamo
        ],
        'latin': [
            (0x0000, 0x024F+1),        # 包含基本拉丁字母和扩展
        ]
    }

    lang_counts = {}  # 各语言字符计数器
    total = 0         # 有效字符总数

    # 统计各语言字符数量
    for char in text:
        cp = ord(char)
        lang = None
        
        for lang_name, ranges in language_blocks.items():
            for start, end in ranges:
                if start <= cp < end:
                    lang = lang_name
                    break
            if lang: break
        
        if lang:
            lang_counts[lang] = lang_counts.get(lang, 0) + 1
            total += 1

    # 没有有效字符视为一致
    if total == 0:
        return True

    # 处理主要语言逻辑
    if main_lang is not None:
        if main_lang not in lang_counts:
            return False
    else:
        main_lang = max(lang_counts, key=lambda k: lang_counts[k])

    # 检查主要语言比例是否达到阈值
    main_ratio = lang_counts[main_lang] / total
    if main_ratio < threshold:
        return False

    return True
def add_arrays(a, b):
    # 使用列表推导式将两个数组的对应元素相加
    return [x + y for x, y in zip(a, b)]

In [ ]:

def validate_and_execute_valite_answer(code_str,answer_type):
    # print(code_str)
    # 超时时间配置（秒）
    MAX_EXECUTION_TIME = 5  
    # 创建通信队列
    result_queue = multiprocessing.Queue()

    try:
        if "```python" in code_str:
            matches=extract_python_code_blocks(code_str)
            if len(matches)>=1 and len(matches[0])>0:
                code_obj = compile(matches[0], '<string>', 'exec')
            else:
                return ""
        else:
        #     return ""
            code_obj = compile(code_str, '<string>', 'exec')
    except SyntaxError as e:
        # return {
        #     "compiled": False,
        #     "result": f"SyntaxError: {e.msg} (line {e.lineno}, offset {e.offset})"
        # }
        result=f"SyntaxError: {e.msg} (line {e.lineno}, offset {e.offset})"
        print(result)
        return ""
    except Exception as e:
        # return {
        #     "compiled": False,
        #     "result": f"Compile Error: {str(e)}"
        # }
        result=f"Compile Error: {str(e)}"
        print(result)
        return ""
    
    # 创建执行进程
    p = multiprocessing.Process(
        target=validate_and_execute_python,
        args=(code_str, result_queue,code_obj)
    )
    
    try:
        p.start()
        p.join(MAX_EXECUTION_TIME)  # 设置超时
        
        if p.is_alive():
            p.terminate()
            p.join()
            return "非数字格式"
            
        if result_queue.empty():
            return {"compiled": False, "result": "未知错误"}
            
        output=result_queue.get()
        if answer_type=='digit':
            print(output)
            num_arr=extract_numbers(output)
            if len(num_arr)>0:
                output=str(num_arr[-1])
        
            return safe_convert(output)
        elif answer_type=='one_d_array':
            print(output)
            num_arr=extract_data_from_string(output,answer_type)
            if len(num_arr)>0:
                output=num_arr
            else:
                output="非数字格式"
            
            return output
        
        elif answer_type=='two_d_array':
            print(code_str)
            print(output)
            num_arr=extract_data_from_string(output,answer_type)
            if len(num_arr)>0:
                output=num_arr
            else:
                output="非数字格式"
        
            return output
        
    finally:
        if p.is_alive():
            p.terminate()
def _execute_code(code_str, result_queue):
    # 重定向输出
    sys.stdout = captured_out = io.StringIO()
    sys.stderr = captured_err = io.StringIO()
    
    try:
        # 第一阶段：编译验证
        code_obj = compile(code_str, '<string>', 'exec')
        
        # 第二阶段：创建安全沙箱
        safe_globals = {
           
        }
        
        # 第三阶段：执行代码
        exec(code_obj, safe_globals)
        
        # 合并输出
        output = captured_out.getvalue() + captured_err.getvalue()
        
        result_queue.put({
            "compiled": True,
            "executed": True,
            "result": output.strip()
        })
        
    except SyntaxError as e:
        result_queue.put({
            "compiled": False,
            "result": f"SyntaxError: {e.msg} (line {e.lineno})"
        })
    except Exception as e:
        result_queue.put({
            "compiled": True,
            "executed": False,
            "result": f"Runtime Error: {str(e)}"
        })
    finally:
        sys.stdout = sys.__stdout__
        sys.stderr = sys.__stderr__
def strict_format_reward_func(completions, **kwargs) -> list[float]:
    """Reward function that checks if the completion has a specific format."""
    pattern = r"^<think>.*?</think>\s*<answer>.*?</answer>$"
    responses = [completion[0]["content"] for completion in completions]
    matches = [re.match(pattern, '<think>'+r, flags=re.DOTALL) for r in responses]
    return [0.5 if match else 0.0 for match in matches]

def soft_format_reward_func(completions, **kwargs) -> list[float]:
    """Reward function that checks if the completion has a specific format."""
    pattern = r"<think>.*?</think>\s*<answer>.*?</answer>"
    responses = [completion[0]["content"] for completion in completions]
    matches = [re.match(pattern, r, flags=re.DOTALL) for r in responses]
    return [0.5 if match else 0.0 for match in matches]
def extract_python_code_blocks(text):
    # 正则表达式模式（注意使用 re.DOTALL 来匹配换行符）
    pattern = re.compile(r'```python\s+(.*?)\s*```', re.DOTALL)
    
    # 查找所有匹配项
    matches = pattern.findall(text)
    return matches
def validate_python(code_str):
    # 第一阶段：编译验证
    
    try:
        # print(code_str)
        matches=extract_python_code_blocks(code_str)
        if len(matches)>=1 and 'print' in matches[0]:
            code_obj = compile(matches[0], '<string>', 'exec')
            # print(matches[0])
            return True
        else:
            code_obj = compile(code_str, '<string>', 'exec')
            if 'print' in code_str:
                # print(code_str)
                return True
            
    except SyntaxError as e:
        return False
        # return {
        #     "compiled": False,
        #     "result": f"SyntaxError: {e.msg} (line {e.lineno}, offset {e.offset})"
        # }
    return False
import sys
import io
def extract_numbers(s):
    # 匹配整数和浮点数的正则表达式，包括正负号
    pattern = r'[-+]?(?:\d+\.\d*|\.\d+|\d+)'
    matches = re.findall(pattern, s)
    numbers = []
    for num_str in matches:
        if '.' in num_str:
            # 转换为浮点数
            numbers.append(float(num_str))
        else:
            # 转换为整数
            numbers.append(int(num_str))
    return numbers
def extract_data_from_string(s, data_type):
    """
    从字符串中提取指定类型的数据。
    
    参数:
    s (str): 输入的字符串。
    data_type (str): 要提取的数据类型，可选 'digit', 'one_d_array', 'two_d_array'。
    
    返回:
    list: 包含提取数据的列表。数字返回整数列表，数组返回列表的列表。
    
    异常:
    ValueError: 当data_type参数无效时抛出。
    """
    # 定义正则表达式匹配模式
    pattern = r'\[\s*(\d+)\s*,\s*(\d+)\s*\]|\[\s*(\d+)\s*\]|(\d+)'

    
    # 初始化结果容器
    digits = []
    one_d_arrays = []
    two_d_arrays = []
    
    for match in re.finditer(pattern, s):
        # 处理二位数组
        if match.group(1) is not None and match.group(2) is not None:
            num1 = int(match.group(1))
            num2 = int(match.group(2))
            two_d_arrays.append([num1, num2])
        # 处理一位数组
        elif match.group(3) is not None:
            num = int(match.group(3))
            one_d_arrays.append([num])
        # 处理独立数字
        elif match.group(4) is not None:
            num = int(match.group(4))
            digits.append(num)
    
    # 根据请求的类型返回结果
    if data_type == 'digit':
        return digits
    elif data_type == 'one_d_array':
        return one_d_arrays
    elif data_type == 'two_d_array':
        return two_d_arrays
    else:
        raise ValueError("无效的数据类型。可选值：'digit', 'one_d_array', 'two_d_array'")
def validate_and_execute_python(code_str, result_queue,code_obj):
    # 第一阶段：编译验证
    # try:
    #     matches=extract_python_code_blocks(code_str)
    #     if len(matches)>=1 and len(matches[0])>20:
    #         # print(matches[0])
    #         code_obj = compile(matches[0], '<string>', 'exec')
    #     else:
    #         result_queue.put("")
    #         return
    # except SyntaxError as e:
    #     # return {
    #     #     "compiled": False,
    #     #     "result": f"SyntaxError: {e.msg} (line {e.lineno}, offset {e.offset})"
    #     # }
    #     result=f"SyntaxError: {e.msg} (line {e.lineno}, offset {e.offset})"
    #     print(result)
    #     result_queue.put("")
    #     return
    # except Exception as e:
    #     # return {
    #     #     "compiled": False,
    #     #     "result": f"Compile Error: {str(e)}"
    #     # }
    #     result=f"Compile Error: {str(e)}"
    #     print(result)
    #     result_queue.put("")
    #     return

    
    # 第二阶段：执行代码
    old_stdout = sys.stdout
    sys.stdout = captured_output = io.StringIO()
    
    try:
        exec(code_obj, {})  # 使用空的全局命名空间
    except Exception as e:
        sys.stdout = old_stdout
        # return {
        #     "compiled": True,
        #     "executed": False,
        #     "result": f"Runtime Error: {str(e)}"
        # }
        result=f"Runtime Error: {str(e)}"
        print(result)
        result_queue.put("")
        return
    else:
        output = captured_output.getvalue()
        sys.stdout = old_stdout
        result_queue.put(output)
        # return {
        #     "compiled": True,
        #     "executed": True,
        #     "result": output.strip()
        # }
        #可选 'digit', 'one_d_array', 'two_d_array'。
        # print(answer_type)
        # print(output)
       
    finally:
        sys.stdout = old_stdout

def python_reward_func(completions, **kwargs) -> list[float]:
    """Reward function that checks if the completion has a specific format."""
    # pattern = r"^<think>.*?</think>\s*<answer>.*?</answer>$"
    responses = [completion[0]["content"] for completion in completions]
    matches = [validate_python(extract_xml_answer(r)) for r in responses]
    return [0.3 if match else 0.0 for match in matches]

def python_reward_result_type_func(completions,answer_type, **kwargs) -> list[float]:
    """Reward function that checks if the completion has a specific format."""
    pattern = r"^<think>.*?</think>\s*<answer>.*?</answer>$"
    responses = [completion[0]["content"] for completion in completions]
    matches = [re.match(pattern, r, flags=re.DOTALL) and validate_and_execute_valite_answer(extract_xml_answer(r),a_type)!="非数字格式" for r,a_type in zip(responses,answer_type)]
    return [2 if match else 0.0 for match in matches]
import math
def safe_convert(s):
    try:
        return int(s)
        
    except ValueError:
        try:
            temp_num=float(s)
            if not math.isfinite(temp_num):
                return "非数字格式"
            return round(temp_num)
        except ValueError:
            return "非数字格式"
            
def zipngram(text: str, ngram_size: int):
        words = text.lower().split()
        return zip(*[words[i:] for i in range(ngram_size)])
def extract_xml_think(text: str) -> str:
    if check_answer_tags(text):
        answer = text.split("<think>")[-1]
        answer = answer.split("</think>")[0]
        return answer.strip()
    else:
        return ''
def chinese_reward(completions, **kwargs) -> list[float]:
    contents = [completion[0]["content"] for completion in completions]
    rewards = []
    for r in contents:
        temp_str=r
        endIndex=20
        if len(temp_str)<20:
            endIndex=len(temp_str)
        if is_language_consistent(temp_str[:endIndex-1],threshold=0.4, main_lang="chinese"):
            rewards.append(1)
        else:
            rewards.append(0)
    return rewards
def repetition_penalty_reward(completions, **kwargs) -> list[float]:
    ngram_size: int=3
    max_penalty: float=-1.0
    """
    reward function the penalizes repetitions
    ref implementation: https://github.com/eddycmu/demystify-long-cot/blob/release/openrlhf/openrlhf/reward/repetition.py

    Args:
        completions: List of model completions
    """

    contents = [completion[0]["content"] for completion in completions]
    rewards = []
    for completion in contents:
        if completion == "":
            rewards.append(0.0)
            continue
        if len(completion.split()) < ngram_size:
            rewards.append(0.0)
            continue

        ngrams = set()
        total = 0
        for ng in zipngram(completion, ngram_size):
            ngrams.add(ng)
            total += 1

        scaling = 1 - len(ngrams) / total
        reward = scaling * max_penalty
        rewards.append(reward)
    return rewards

winCount=0
tryCount=0
def python_reward_correct_func(prompts,completions, answer,answer_type, **kwargs) -> list[float]:
    """Reward function that checks if the completion has a specific format."""
    pattern = r"^<think>.*?</think>\s*<answer>.*?</answer>$"
    q = prompts[0][-1]['content']
    responses = ['<think>\n'+completion[0]["content"] for completion in completions]
    anwer_arr=[]
    for r in responses:
        # if re.match(pattern, r, flags=re.DOTALL):# and is_language_consistent(r)
        # temp_r=extract_numbers(extract_xml_answer(r))
        # if len(temp_r)>0:
        #     anwer_arr.append(temp_r[-1])
        # else:
        #     anwer_arr.append('no')
       
        anwer_arr.append('no')
            
    
    matches=[]
    print(responses[0])
    for r,a_type in zip(responses,answer_type):
        
        # if re.match(pattern, r, flags=re.DOTALL):
            # print(extract_xml_code(r))
        
        output=validate_and_execute_valite_answer(extract_xml_answer(r),a_type)
        if output!="非数字格式":
            matches.append(output)
        else:
            matches.append("no")
       
        # matches.append("no")

        # else:
        #     matches.append("no")
    # matches = [if re.match(pattern, r, flags=re.DOTALL) and ==safe_convert(answer) for r in responses]
    # print(f"Response:\n{responses[i]}")
    # formatScore=[-0.1  if re.match(pattern, r, flags=re.DOTALL)==False or len(extract_python_code_blocks(extract_xml_answer(r)))==0 else 0  for r in responses]
    result=[]
    for r, a,a2 in zip(matches, answer,anwer_arr):
        if r==a and a==a2:
            result.append(4)
        elif r == a   : #or     a==a2
            result.append(2)
        else:
            # if r=='no' and a2=='no':
            #     result.append(-4)
            # # elif r=='no' or a2=='no':
            # #     result.append(-2)
            # else:
            result.append(0)
        
    # result=[2.0 if r == a or a==a2 else 0.0 for r, a,a2 in zip(matches, answer,anwer_arr)]
    global winCount,tryCount
    if sum(result)!=0:
        winCount+=1
    tryCount+=1
    len_arr=[]
    # correctness=[]
    for i, score in enumerate(result):
        if score >= 2.0:
            print('-'*20)
            print(f"Response:\n{responses[i]}")
            # correctness.append(True)
        # else:
        #     correctness.append(False)
        len_arr.append(len(responses[i]))
        

    # lengths = [len(content) for content in responses]
    # min_len = min(lengths)
    # max_len = max(lengths)

    # If all responses have the same length, return zero rewards
    # if max_len == min_len:
    #     return [0.0] * len(completions)

    # len_rewards = []
    # for length, is_correct in zip(lengths, correctness):
    #     lambda_val = 0.5 - (length - min_len) / (max_len - min_len)

    #     if is_correct:
    #         reward = lambda_val
    #     else:
    #         reward = min(0, lambda_val)

    #     len_rewards.append(float(reward))

    # result = [x + y for x, y in zip(result, len_rewards)]
    print(f"Question:\n{q}")
    print('realAnswer:')
    print(answer)
    print(matches)
    print(anwer_arr)
    print('correct:',result)
    print(len_arr)
    print('winCount:',winCount)
    print('tryCount:',tryCount)
    if tryCount!=0:
        print('winRate:',round(winCount*100/tryCount))

    if sum(result)!=0:
        temp_arr=chinese_reward(completions)
        print('chinese:',temp_arr)
        result=add_arrays(result,temp_arr)
        temp_arr=xmlcount_reward_func(completions)
        print('xmlcount_reward_func:',temp_arr)
        result=add_arrays(result,temp_arr)
        temp_arr=strict_format_reward_func(completions)
        print('strict_format_reward_func:',temp_arr)
        result=add_arrays(result,temp_arr)
        temp_arr=repetition_penalty_reward(completions)
        print('repetition_penalty_reward:',temp_arr)
        result=add_arrays(result,temp_arr)
        temp_arr=python_reward_func(completions)
        result=add_arrays(result,temp_arr)
        print('python_reward_func:',temp_arr)
    return result
def test_correct_func(prompts,completions, answer,answer_type, **kwargs) -> list[float]:
    """Reward function that checks if the completion has a specific format."""
    pattern = r"^<think>.*?</think>\s*<answer>.*?</answer>\s*<code>.*?</code>$"
    q = prompts[0][-1]['content']
    responses = ['<think>\n'+completion[0]["content"] for completion in completions]
    anwer_arr=[]
    for r in responses:
        question=f"""分析下面回答，回答中有没有说计算方差前，先要计算连续价格差。如果有就返回"1",没有就返回"0"
            {r}
        """
        an_str=get_answer(question)
        print("start------------")
        print(an_str)
        temp_r=extract_numbers(an_str)
        print(temp_r)
        if len(temp_r)>=1:
            anwer_arr.append(temp_r[-1])
            print(anwer_arr)
        else:
            anwer_arr.append('no')
    
    matches=[]
    # print(responses[0])
    for r,a_type in zip(responses,answer_type):
        
        # if re.match(pattern, r, flags=re.DOTALL):
            # print(extract_xml_code(r))
        output=validate_and_execute_valite_answer(extract_xml_code(r),a_type)
    
        if output!="非数字格式":
            matches.append(output)
        else:
            matches.append("no")
        # else:
        #     matches.append("no")
    # matches = [if re.match(pattern, r, flags=re.DOTALL) and ==safe_convert(answer) for r in responses]
    # print(f"Response:\n{responses[i]}")
    # formatScore=[-0.1  if re.match(pattern, r, flags=re.DOTALL)==False or len(extract_python_code_blocks(extract_xml_answer(r)))==0 else 0  for r in responses]
    result=[]
    for r, a,a2 in zip(matches, answer,anwer_arr):
        if a2==1:
            result.append(4)
        else:
            result.append(0)
        # if r==a and a==a2:
        #     result.append(4)
        # elif r == a or a==a2:
        #     result.append(2)
        # else:
        #     # if r=='no' and a2=='no':
        #     #     result.append(-4)
        #     # # elif r=='no' or a2=='no':
        #     # #     result.append(-2)
        #     # else:
        #     result.append(0)
        
    # result=[2.0 if r == a or a==a2 else 0.0 for r, a,a2 in zip(matches, answer,anwer_arr)]

    len_arr=[]
    # correctness=[]
    for i, score in enumerate(result):
        if score >= 2.0:
            print('-'*20)
            print(f"Response:\n{responses[i]}")
            # correctness.append(True)
        # else:
        #     correctness.append(False)
        len_arr.append(len(responses[i]))
        

    # lengths = [len(content) for content in responses]
    # min_len = min(lengths)
    # max_len = max(lengths)

    # If all responses have the same length, return zero rewards
    # if max_len == min_len:
    #     return [0.0] * len(completions)

    # len_rewards = []
    # for length, is_correct in zip(lengths, correctness):
    #     lambda_val = 0.5 - (length - min_len) / (max_len - min_len)

    #     if is_correct:
    #         reward = lambda_val
    #     else:
    #         reward = min(0, lambda_val)

    #     len_rewards.append(float(reward))

    # result = [x + y for x, y in zip(result, len_rewards)]
    print(f"Question:\n{q}")
    print('realAnswer:')
    print(answer)
    print(matches)
    print(anwer_arr)
    print(result)
    print(len_arr)
    return result
import math_verify
def validate_equation(equation_str, available_numbers):
    """Validate that equation only uses available numbers and each number once."""
    try:
        # Extract all numbers from the equation
        numbers_in_eq = [int(n) for n in re.findall(r'\d+', equation_str, flags=re.DOTALL)]
        
        # Check if all numbers in equation are available
        available_numbers = sorted(available_numbers)
        numbers_in_eq = sorted(numbers_in_eq)
        
        # Each number should be used exactly once
        return numbers_in_eq == available_numbers
    except:
        return False
def evaluate_equation(equation_str):
    """Safely evaluate the arithmetic equation using eval() with precautions."""
    try:
        # Define a regex pattern that only allows numbers, operators, parentheses, and whitespace
        allowed_pattern = r'^[\d+\-*/().\s]+$'
        if not re.match(allowed_pattern, equation_str, flags=re.DOTALL):
            raise ValueError("Invalid characters in equation.")

        # Evaluate the equation with restricted globals and locals
        result = eval(equation_str, {"__builtins__": None}, {})
        return result
    except Exception as e:
        return None
def check_think_tags(text):
    return '<think>' in text and '</think>' in text

def extract_xml_think(text: str) -> str:
    if check_think_tags(text):
        answer = text.split("<think>")[-1]
        answer = answer.split("</think>")[0]
        return answer.strip()
    else:
        return ''
def remove_after_equal(s):
    index = s.find('=')
    return s[:index] if index != -1 else s
def replace_chinese_brackets_re(text):
    return re.sub(r'[（）]', lambda x: '(' if x.group() == '（' else ')', text)
import xml.etree.ElementTree as ET

def extract_all_elements(xml_str):
    """
    解析完整XML结构并提取三大核心元素
    """
    try:
        # 自动添加根节点以兼容无根节点的情况
        wrapped_xml = f"<root>{xml_str}</root>"
        root = ET.fromstring(wrapped_xml)
    except ET.ParseError:
        return None

    # 提取核心元素
    result = {
        'analysis': (root.findtext('analysis') or '').strip(),
        'strategies': [],
        'answer': (root.findtext('answer') or '').strip()
    }

    # 处理策略迭代
    strategy_arr = root.find('.//strategy_arr')
    if strategy_arr is not None:
        for strategy_node in strategy_arr.findall('strategy_one'):
            iteration = strategy_node.get('iteration')
            validation_node = strategy_node.find('validation')

            strategy_data = {
                'iteration': iteration,
                'condition': strategy_node.get('condition'),
                'strategy': (strategy_node.findtext('strategy') or '').strip(),
                'execution': (strategy_node.findtext('execution') or '').strip(),
                'reflect': (strategy_node.findtext('reflect') or '').strip(),
                'validation': {
                    'status': validation_node.get('status') if validation_node is not None else '',
                    'content': (validation_node.text or '').strip() if validation_node is not None else ''
                }
            }
            result['strategies'].append(strategy_data)

    return result


In [ ]:
import requests

from openai import OpenAI

client = OpenAI(
    base_url='http://192.168.3.129:11434/v1',
    api_key='ollama'  # 占位符，实际不需要验证
)
def check_result_tags(text):
    return '<result>' in text and '</result>' in text
def extract_xml_result(text: str) -> str:
    if check_result_tags(text):
        answer = text.split("<result>")[-1]
        answer = answer.split("</result>")[0]
        return answer.strip()
    else:
        return ''
def get_answer(question):
    global client
    total_win=[]
    t_count=1
    for i in range(t_count):
        response = client.chat.completions.create(
        model="deepseek-r1:latest",
        messages=[{"role": "user", "content": question}],
        max_tokens=500,
        # temperature=0.3  # 0=确定性强，1=随机性强
        )
        res=response.choices[0].message.content
        num_arr=extract_numbers(res)
        if num_arr[-1]==1:
            total_win.append(1)
        else:
            total_win.append(0)
        # print('r1_think:',res)
    
    print('total_win:',total_win)
    if sum(total_win)>=t_count:
        return True,res
    else:
        return False,res
# def get_answer(question):
#     """
#     向指定的API接口发送问题并返回答案
    
#     参数：
#         question (str): 要查询的问题文本
    
#     返回：
#         str: 接口返回的答案内容，若请求失败返回错误信息
#     """
#     url = "http://192.168.3.126:8000/generate"
#     headers = {
#         "Content-Type": "application/json"
#     }
#     data = {
#         "content": question
#     }
    
#     try:
#         response = requests.post(url, headers=headers, json=data, timeout=200)
#         if response.status_code == 200:
#             result = response.json()
#             return result.get("content", "响应中未找到答案内容")
#         else:
#             return f"请求失败，状态码：{response.status_code}\n响应内容：{response.text}"
#     except requests.exceptions.RequestException as e:
#         return f"请求发生异常：{str(e)}"
#     except json.JSONDecodeError:
#         return "响应内容解析失败"

# # 示例用法
# if __name__ == "__main__":
#     answer = get_answer("9.9和9.11谁大")
#     print("\n最终答案：")
#     print(answer)


In [ ]:
# dataset = load_dataset('json', data_files='all_anomaly_data.json')
# def make_conversation(example):
#     target = example['anomaly_index']
#     numbers = example['time_array']
#     prop=f"""分析连续时间数据{numbers}，找出时间中的异常时间。答案是时间对应的index值.例如<answer>1</answer>."""    
#     # print(prop)
#     return {
#         "prompt": [
#             {"role": "system", "content": SYSTEM_PROMPT},
#             {"role": "user", "content": prop},
#         ],
#         "answer":str(target),
#         "type":"yi_time"
#     }
# dataset=dataset.map(make_conversation)['train']

In [ ]:
# import random
# lizi="""
# 异常连锁反应的形成机制需满足三个核心条件：首先，连续异常事件的时间间隔必须处于预设的有效时间窗口内；其次，初始异常的触发逻辑与后续异常需保持逻辑关联性，形成因果传导链；最后，整个异常序列应呈现出可追溯的规律性特征，具体表现为异常类型、触发顺序和影响范围等维度存在可预测的关联模式。这种机制的本质是通过时间关联性、逻辑一致性和模式规律性三个维度的耦合作用，将离散异常事件转化为具有系统级影响的连锁反应。

# 找出异常连锁反应，并把构成连锁反应的异常索引值放到<answer>标签内,答案格式<answer>[1,4,9]</answer>
# 数据内容介绍:[[索引,值]]
# 输入数据:

# """

# data=[]
# for i in range(100):
#     # 生成两个3到4位的随机整数
#     num1 = random.randint(100, 500)
#     num2 = random.randint(100, 500)
#     q=f'{num1}*{num2}=?'
#     data.append({"question": q, "answer": str(num1*num2)})
# # 创建数据集
# dataset = Dataset.from_list(data)

# dataset = load_dataset('json', data_files='anomalies_data.json、')

In [ ]:
# import random
lizi="""
分析数据中的异常.(用python代码回答.print(答案),答案格式[[价格变化,成交量变化]])
期货数据内容介绍:[[价格变化,成交量变化]]
输入数据:
"""
# tempStr="""
# 异常连锁反应的形成机制需满足三个核心条件：首先，连续异常事件的时间间隔必须处于预设的有效时间窗口内；其次，初始异常的触发逻辑与后续异常需保持逻辑关联性，形成因果传导链；最后，整个异常序列应呈现出可追溯的规律性特征，具体表现为异常类型、触发顺序和影响范围等维度存在可预测的关联模式。这种机制的本质是通过时间关联性、逻辑一致性和模式规律性三个维度的耦合作用，将离散异常事件转化为具有系统级影响的连锁反应。

# 二、期货市场典型异常连锁类型
# 1. 量价累积型（正反馈模式）
# - 成交量持续放大
# - 价格呈现单向累积趋势

# 2. 阻力突破型（震荡蓄能模式）
# - 成交量脉冲式放大
# - 价格呈现震荡反转特征
# - 存在静态强阻力位
# """
data=[]

tempData=[]
# tempData.append([[100, 800], [7, 67], [3, 39], [-8, 74], [2, 36], [-40, 799], [9, 21], [0, 71], [30, 355], [5, 50], [-3, 64], [5, 59], [-8, 94], [-9, 1], [5, 2], [9, 8], [3, 42], [9, 82], [10, 11], [0, 100]])
# tempData.append([[26, 306], [5, 427], [0, 451], [210, 3240], [29, 285], [25, 231], [16, 271], [29, 399], [-7, 389], [26, 482], [-19, 338], [-15, 402], [21, 467], [-170, 2590], [-1, 229], [111, 1400], [9, 230], [-27, 270], [-14, 426], [-19, 380]])
# tempData.append([[-41, 443], [130, 4650], [1, 323], [30, 318], [130, 3860], [-31, 245], [49, 495], [27, 414], [11, 324], [0, 439], [47, 366], [-117, 2480], [-38, 473], [49, 294], [-37, 395], [27, 358], [9, 409], [-24, 425], [-26, 426], [-50, 254]])
tempData.append([[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[9,100],[8,50],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1]])
tempData.append([[1,1],[1,1],[1,1],[1,1],[99,100],[1,1],[1,1],[1,1],[1,1],[77,200],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1]])

anserArr=[]
# anserArr.append([[100, 800],[-40,799],[30, 355]])
# anserArr.append([[210, 3240],[-170, 2590],[111, 1400]])
# anserArr.append([[130, 4650],[130, 3860],[-117, 2480]])
anserArr.append([[9,100],[8,50]])
anserArr.append([[99,100],[77,200]])
for i in range(len(tempData)):
    data.append({"question": lizi+str(tempData[i]), "answer": anserArr[i],'answer_type':'two_d_array'})
# 创建数据集
# dataset = Dataset.from_list(data)
# print(dataset)
# dataset = load_dataset('json', data_files='anomalies_data.json')

In [ ]:
# temp_index=0
def make_conversation(example):
    # global temp_index
    # temp_index+=1
    # print(temp_index)
    # target = example['question']
    # numbers = example['time_array']
    # prop=f"""分析连续时间数据{numbers}，找出时间中的异常时间。答案是时间对应的index值.例如<answer>1</answer>."""    
    # print(prop)
    return {
            "prompt": [
                {"role": "system", "content": SYSTEM_PROMPT},
                {"role": "user", "content": str(example['question'])},
            ],
            "answer":example['answer'],
        }
# dataset=dataset.map(make_conversation)['train']
# dataset=dataset.map(make_conversation)
# print(dataset)

In [ ]:
from trl import GRPOConfig,GRPOTrainer
max_prompt_length=300
training_args = GRPOConfig(
    use_vllm = True, # use vLLM for fast inference!
    learning_rate = 5e-6,
    adam_beta1 = 0.9,
    adam_beta2 = 0.99,
    weight_decay = 0.1,
    warmup_ratio = 0.1,
    lr_scheduler_type = "cosine",
    optim = "paged_adamw_8bit",
    logging_steps = 1,
    bf16 = is_bfloat16_supported(),
    fp16 = not is_bfloat16_supported(),
    per_device_train_batch_size = 1,
    gradient_accumulation_steps = 1, # Increase to 4 for smoother training
    num_generations = 4, # Decrease if out of memory
    max_prompt_length = max_prompt_length,
    max_completion_length = (max_seq_length-max_prompt_length),
    num_train_epochs = 4, # Set to 1 for a full training run
    # max_steps = 100,
    # save_steps =100,
    max_grad_norm = 0.1,
    report_to = "none", # Can use Weights & Biases
    output_dir = "outputs",
)

In [ ]:
import re

from lxml import etree

def validate_xml_structure(text):
    try:
        root = etree.fromstring(f"<root>{text}</root>")
        tags = [elem.tag for elem in root]
        
        # 检查answer的数量和位置
        if tags.count('answer') != 1 or tags[-1] != 'answer':
            return False,0
        
        preceding_tags = tags[:-1]
        
        # 检查至少3个交替对且总数为偶数
        if len(preceding_tags) < 2 or len(preceding_tags) % 2 != 0:
            return False,0
        
        # 验证每对都是think在前reflect在后
        for i in range(0, len(preceding_tags), 2):
            if preceding_tags[i] != 'think' or preceding_tags[i+1] != 'reflect':
                return False,0
        
        return True,(len(preceding_tags)-1)/2
    except etree.XMLSyntaxError:
        return False,0


# 测试示例
valid_example = """<think>
内容1
</think>
<reflect>
内容2
</reflect>
<think>
内容3
</think>
<reflect>
内容4
</reflect>
<think>
内容5
</think>
<reflect>
内容6
</reflect>
<think>
内容5
</think>
<reflect>
内容6
</reflect>
<answer>
答案
</answer>"""
v,think_count=validate_xml_structure(valid_example)
print(v)  # 输出: True

def accuracy_reward_fn(completions, target,nums,prob, **kwargs):
    global winCount,tryCount
    tryCount+=1
    responses = [completion[0]["content"] for completion in completions]
    # len_arr=[len(res) for res in responses]
    # avg=sum(len_arr)/len(len_arr)
    # avg=avg*1.2
    result=[]
    print('-------------------------------------------------------------------')
    print(responses[0])
    is_find=False
    for full_solution,num_arr,right,p in zip(responses,nums,target,prob):
        temp=0.0
        v,think_count=validate_xml_structure(full_solution)
        if v:
            temp+=2
            add=think_count*0.2
            if add>1:
                add=1
            temp+=add
        
        equation=extract_xml_answer(full_solution)
        equation=remove_after_equal(equation)
        equation=replace_chinese_brackets_re(equation)
        # think_str=extract_xml_think(full_solution)
        if len(equation) >0:
            if validate_equation(equation, num_arr):
                # temp+=1
                print('equation:',equation)
                res= evaluate_equation(equation)
                print('equation:',equation)
                if res != None:
                  
                    if abs(res - right) < 1e-5:
                        temp+=3.0
                        print('full_solution:',full_solution)
                        is_find=True

                # if len(think_str)!=0:
                #     # question=f"""分析下面思考过程，思考过程有没有进行多路径思考并完整的进行了验证,如果有就返回"1",没有就返回"0",把返回结果放入<result></result>内。\n问题:{p} 思考过程:'{think_str}'"""
                #     # question=f"""检查下面思考过程，1.有没有进行完整思考并进行计算验证.2.最后有没有给出确定答案.3.有没有进行多次试错.4.对得出的结果进行反思验证.如果全部4条都做到就返回"1",没有就返回"0",把返回结果放入<result></result>内。 \n思考过程:'{think_str}'"""
                #     question=f"""分析下面思考过程，思考过程有没有反思总结,如果有就返回"1",没有就返回"0",把返回结果放入<result></result>内。\n思考过程:\n'{think_str}'"""
        
                #     an,res= get_answer(question)
                #     if an:
                #         temp+=10
                #         print('多路径思考并反思验证:',think_str)
                #         print('验证思路:',res)
                #         print('结果:',equation)
                #         print('nums:',num_arr)
            # else:
            #     allowed_pattern = r'^[\d+\-*/().\s]+$'
            #     if re.match(allowed_pattern, equation, flags=re.DOTALL):
            #         temp+=0.5
            #     print(f"Invalid equation")
       
        
            # question=f"""分析下面思考过程，回答中有没有进行反思验证,如果有就返回"1",没有就返回"0"\n输入:'{think_str}'"""
            # an = get_answer(question)
            # temp_arr=extract_numbers(an)
            # if len(temp_arr)==1 and temp_arr[0]==1:
            #     temp+=1
            #     print('反思验证:',think_str)
            #     print('结果:',equation)
       
        result.append(temp)
    if is_find:
        winCount+=1
    print('score:',result)
    print('winRate:',winCount*100/tryCount)
    print('winCount:',winCount,":tryCount:",tryCount)
    return result

In [ ]:

SYSTEM_PROMPT = """
你是一个专业的问题解决AI助手，遵循严格的响应格式。当遇到问题时，请：
先进行深度推理(<think>标签内)
反思总结(<reflect>标签内)
进行深度推理(<think>标签内)
反思总结(<reflect>标签内)
进行深度推理(<think>标签内)
反思总结(<reflect>标签内)
进行深度推理(<think>标签内)
反思总结(<reflect>标签内)
...直到有准确答案
给出答案(<answer>标签内)

请按照以下格式进行回应：
<think>\n...\n</think>\n<reflect>\n...\n</reflect>\n<think>\n...\n</think>\n<reflect>\n...\n</reflect>\n...<answer>\n...\n</answer>
"""

goodArr=[]
def format_prompt(ex) -> Dataset:

    numbers=ex['nums']
    target=ex['target']
    # problem = f"使用数字 {numbers}，创建一个等于 {target} 的等式。你可以使用基本算术运算(+、-、*、/)，并且每个数字只能使用一次。在 <think> 和 </think> 标签中展示你的思考过程，并在 <answer> 和 </answer> 标签中返回最终答案，例如 <answer> (1 + 2) / 3 </answer>。"
    problem = f"使用数字 {numbers}，创建一个等于 {target} 的等式。你可以使用基本算术运算(+、-、*、/)，并且每个数字只能使用一次。答案格式例如 <answer> (1 + 2) / 3 </answer>。"

    
    # prompt = base_pro + '\n' + problem

    # formatted_prompt = tokenizer.apply_chat_template([{'role': 'user', 'content': prompt}], tokenize=False, add_generation_prompt=True)

    # ex['numbers'] = torch.tensor(ex['numbers'])
    ex['prompt'] = [
            {'role': 'system', 'content': SYSTEM_PROMPT},
            {'role': 'user', 'content': problem}
        ]
    # ex['formatted_prompt'] = formatted_prompt
    ex['prob']=problem
    # print(len(numbers))
    if len(numbers)<=3:
        goodArr.append(ex)
    return ex

   
    
    return data # type: ignore
# print(dataset)

# dataset = load_dataset('nlile/24-game', split='train').map(format_prompt, remove_columns=['solutions']).train_test_split(test_size=50, seed=3000)
dataset = load_dataset('Jiayi-Pan/Countdown-Tasks-3to4-Unique', split='train').map(format_prompt)


In [59]:
dataset=Dataset.from_list(goodArr[0:300])
# t=goodArr[:200]
print(len(dataset))

300


In [62]:
winCount=0
tryCount=0
# 包含 system 角色的完整模板
# tokenizer.chat_template = """
# {% for message in messages %}
#   <|im_start|>{{ message.role }}
#   {{ message.content }}<|im_end|>
# {% endfor %}
#   <|im_start|>assistant<think>\n
# """
# from my_trainer import 
trainer = GRPOTrainer(
    model = model,
    processing_class = tokenizer,
    reward_funcs = [
        # python_reward_correct_func,
        accuracy_reward_fn
        # chinese_reward,
        # xmlcount_reward_func,
        # strict_format_reward_func,
        # repetition_penalty_reward
        # python_reward_func,
        # python_reward_int_func
        
        # test_correct_func,
        
        # int_reward_func,
        # correctness_reward_func,
    ],
    args = training_args,
    train_dataset = dataset,
)
# trainer.train(resume_from_checkpoint = True)
# trainer.train(resume_from_checkpoint="./outputs/checkpoint-100")  # 指定检查点
# resume_from_checkpoint="./output/checkpoint-1000"
trainer.train()
# trainer.test()

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 300 | Num Epochs = 4 | Total steps = 1,200
O^O/ \_/ \    Batch size per device = 4 | Gradient accumulation steps = 1
\        /    Data Parallel GPUs = 1 | Total batch size (4 x 1 x 1) = 4
 "-____-"     Trainable parameters = 59,867,136/1,758,539,776 (3.40% trained)


-------------------------------------------------------------------
<think>
我们需要使用给定的数字 83 和 49 来构造一个等于 49 的等式。83 这个数字太大，直接除以 49 很可能不是整数，我们需要寻找其他的操作来使结果等于 49。
</think>
<reflect>
我们可以尝试将 83 除以 49，结果不会是整数，所以我们需要尝试其他的方法。83 - 49 的结果是 34，显然不是 49；83 + 49 的结果是 132，离 49 还是远。考虑到 83 本身太大，直接用减法或加法不可能得到 49，我们需要尝试组合这些数字以找到合适的等式。
</reflect>
<think>
如果我们将两个 83 相减，得到的结果是 0。然后用 0 除以剩余的数字 49，得到的结果是 0。0 加上 49 等于 49。
</think>
<reflect>
83 - 83 = 0，然后 0 / 49 = 0，0 + 49 = 49。这样等式就满足了条件。
</reflect>
<think>
我们可以用更复杂的方法来构造等式，但是这个简单的组合已经足够得到答案。
</think>
<reflect>
答案已经找到了，使用数字 83, 83 和 49，我们可以构造等式：83 - 83 / 49 = 49。这个等式是正确的。
</reflect>
<answer>
83 - 83 / 49 = 49
</answer>
score: [2.5, 3.0, 2.7, 3.0]
winRate: 0.0
winCount: 0 :tryCount: 1


-------------------------------------------------------------------
<think>
为了使等式等于 45，我们可以尝试将这些数字组合成一个简单的乘法和加法。由于 45 - 36 = 9，那么我们尝试将 45 分解成 18 + 27。
考虑数字 43 和 71，它们的差值为 28，接近我们需要的 27。因此，43 - 71 = -28，但是我们需要 27。我们可以尝试 43 + 71 - 71 + 43 - 71 = 18 + 27，但这是一个很复杂的等式。
</think>
<reflect>
结合数字 43 和 71 可以形成一个较大的差值，但没有直接的方法使它们的组合等于 45。我们需要找到一个更好的组合方式。
</reflect>
<think>
让我们尝试其他方法。我们可以尝试将 17 作为中间值，让 43 和 71 分别加和减 17。这样，我们可能能够形成 45。
</think>
<reflect>
将数字 17 作为中间值，尝试各种组合方式，但都无法使等式等于 45。
</reflect>
<think>
再尝试一下，我们可以尝试使用 43 进行一系列加减操作，同时保持等式结果为 45。
</think>
<reflect>
我们将数字 43 作为操作对象，尝试进行加减运算，但结果不是 45。
</reflect>
<think>
现在，让我们尝试用一种更直接的方法。我们已知 17 无法单独使用来形成 45，但我们可以尝试通过组合 43 和 71 来形成 45。
</think>
<reflect>
尽管尝试了各种组合，但仍然无法形成等式等于 45。
</reflect>
<think>
最后，让我们尝试另一种方式，将 43 和 71 直接相加，然后减去一个特定的数。
</think>
<reflect>
尝试 43 + 71 - 80 的方式，但结果不是 45。
</reflect>
<think>
我们需要找到一种更直接的方法来形成等式等于 45。让我们重设思路，将 45 分解为更简单的数字组合。
</think>
<reflect>
再次尝试各种方法，找到一个有效等式。
</reflect>
<think>
经过多次尝试，我们发现 45 可以通过 43 + 71 - 71 的方式

TrainOutput(global_step=1200, training_loss=0.0005742296138972354, metrics={'train_runtime': 31715.2649, 'train_samples_per_second': 0.038, 'train_steps_per_second': 0.038, 'total_flos': 0.0, 'train_loss': 0.0005742296138972354})

In [61]:
model.save_lora("qwen_3_25")

In [ ]:

# qe="""
# 分析数据中的异常.(用python代码回答.print(答案),答案格式[[价格变化,成交量变化]])
# 期货数据内容介绍:[[价格变化,成交量变化]]
# 输入数据:
# [[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[4,15],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[9,100],[8,50],[1,1],[1,1],[1,1],[1,1],[1,1],[7,99],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1],[1,1]]
# """

# q2="""
# Simplify and rationalize the denominator: $$\frac{1}{1+ \frac{1}{\sqrt{3}+1}}.$$(用python代码回答.print(答案))
# """
# notGoodCount=0
# for one in noRightArr:
#     # one=noRightArr[5]
#     text = tokenizer.apply_chat_template(one['prompt'],
#     tokenize = False, add_generation_prompt = True)
#     print(one['prompt'])
#     from vllm import SamplingParams
#     sampling_params = SamplingParams(
#         temperature = 0.8,
#         top_p = 0.95,
#         max_tokens = 3024,
#     )
#     loadLoraData=model.load_lora("test_grpo_saved_lora")
#     is_find_good=False
#     for i in range(5):
#         output = model.fast_generate(
#                 text,
#                 sampling_params = sampling_params,
#                 lora_request = loadLoraData,
#                 )[0].outputs[0].text
#         resultV=validate_and_execute_valite_answer(output,'digit')
#         # print('answer:'+str(one['answer']))
#         # print(resultV)
#         if resultV==one['answer']:
#             is_find_good=True
#             print('good')
#             break
#         # print(output)
#     if is_find_good==False:
#         notGoodCount+=1
# print(notGoodCount)

In [ ]:
# model, tokenizer = FastLanguageModel.from_pretrained(
#     model_name = "meta-llama/meta-Llama-3.1-8B-Instruct",
#     # model_name = "./outputs/checkpoint-100",
#     max_seq_length = 1024,
#     load_in_4bit = True, # False for LoRA 16bit
#     fast_inference = True, # Enable vLLM fast inference
#     max_lora_rank = 32,
#     gpu_memory_utilization = 0.6, # Reduce if out of memory
# )


In [ ]:
# text = tokenizer.apply_chat_template([
#     {"role" : "user", "content" : "When \( a < -1 \), the nature of the roots for the equation $$ \left(a^{3}+1\right) x^{2}+\left(a^{2}+1\right) x-(a+1)=0 $$ is: (A) Two negative roots. (B) One positive root and one negative root, with the absolute value of the negative root being larger. (C) One positive root and one negative root, with the absolute value of the negative root being smaller. (D) No real roots."},
# ], tokenize = False, add_generation_prompt = True)

# from vllm import SamplingParams
# sampling_params = SamplingParams(
#     temperature = 0.8,
#     top_p = 0.95,
#     max_tokens = 2024,
# )
# output = model.fast_generate(
#     [text],
#     sampling_params = sampling_params,
#     lora_request = None,
# )[0].outputs[0].text

# output

In [ ]:
# Merge to 16bit
# if False: model.save_pretrained_merged("model", tokenizer, save_method = "merged_16bit",)
# if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "merged_16bit", token = "")

# # Merge to 4bit
# if True: model.save_pretrained_merged("model", tokenizer, save_method = "merged_4bit_forced",)
# if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "merged_4bit", token = "")

# # Just LoRA adapters
# if False: model.save_pretrained_merged("model", tokenizer, save_method = "lora",)
# if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "lora", token = "")

In [ ]:
# model.save_pretrained_merged("model", tokenizer, save_method = "merged_4bit_forced",)

In [ ]:
#恢复训练时加载 Adapter

In [ ]:
# from transformers import AutoModelForSequenceClassification
# from peft import PeftModel, PeftConfig

# # 加载基础模型
# base_model = AutoModelForSequenceClassification.from_pretrained("bert-base-uncased")

# # 加载 Adapter 配置和参数
# peft_config = PeftConfig.from_pretrained("./output/checkpoint-1000")
# peft_model = PeftModel.from_pretrained(
#     base_model,
#     "./output/checkpoint-1000",  # 检查点路径
#     config=peft_config,
#     is_trainable=True  # 启用训练模式
# )

# # 继续训练（需确保加载优化器状态）
# trainer = Trainer(
#     model=peft_model,
#     args=training_args,
#     train_dataset=dataset,
# )
# trainer.train(resume_from_checkpoint=True)  # 自动加载 Adapter 状态

In [ ]:
text = "深度学习的文本生成任务需要注意什么？"
tokens = tokenizer.encode(q, add_special_tokens=False)

print(f"Token数量：{len(tokens)}")  # 输出：15
print(f"Token映射：{tokenizer.convert_ids_to_tokens(tokens)}")
# 输出：['深', '度', '学', '习', '的', '文本', '生', '成', '任', '务', '需', '要', '注', '意', '什么', '？']

In [ ]:
def is_language_consistent(text, threshold=0.2, main_lang="chinese"):
    """判断文本语言是否一致（要求主要语言字符不低于指定比例）
    
    Args:
        text: 待检测文本
        threshold: 主要语言最低要求比例，默认95%
        main_lang: 指定主要语言（可选），如'chinese'、'japanese_kana'等
        
    Returns:
        bool: 是否语言一致
    """
    # 定义各语言的Unicode范围（前闭后开区间）
    language_blocks = {
        'chinese': [
            (0x4E00, 0x9FFF+1),        # CJK Unified Ideographs
            (0x3400, 0x4DBF+1),        # CJK Extension A
            (0x20000, 0x2A6DF+1),      # CJK Extension B
            (0xF900, 0xFAFF+1),        # CJK Compatibility Ideographs
        ],
        'japanese_kana': [
            (0x3040, 0x309F+1),        # Hiragana
            (0x30A0, 0x30FF+1),        # Katakana
        ],
        'korean': [
            (0xAC00, 0xD7AF+1),        # Hangul Syllables
            (0x1100, 0x11FF+1),        # Hangul Jamo
        ],
        'latin': [
            (0x0000, 0x024F+1),        # 包含基本拉丁字母和扩展
        ]
    }

    lang_counts = {}  # 各语言字符计数器
    total = 0         # 有效字符总数

    # 统计各语言字符数量
    for char in text:
        cp = ord(char)
        lang = None
        
        for lang_name, ranges in language_blocks.items():
            for start, end in ranges:
                if start <= cp < end:
                    lang = lang_name
                    break
            if lang: break
        
        if lang:
            lang_counts[lang] = lang_counts.get(lang, 0) + 1
            total += 1

    # 没有有效字符视为一致
    if total == 0:
        return True

    # 处理主要语言逻辑
    if main_lang is not None:
        if main_lang not in lang_counts:
            return False
    else:
        main_lang = max(lang_counts, key=lambda k: lang_counts[k])

    # 检查主要语言比例是否达到阈值
    main_ratio = lang_counts[main_lang] / total
    if main_ratio < threshold:
        return False

    return True



# 检查文本是否包含至少 90% 的中文字符
print(is_language_consistent("中文测试Hello", threshold=0.2, main_lang="chinese"))  # 假设中文占 80% 则返回 False

# 自动检测主语言并检查是否占 95% 以上
print(is_language_consistent("日本語メインの文章"))  # 若日语字符占 100% 则返回 True



In [ ]:
a=[3,2,1]
a=sorted(a)
print(a)